## 💡 这节课会带给你

1. 了解机器学习的基本概念
2. 掌握模型微调/小参数量微调的操作过程
3. 掌握模型微调/小参数量微调关键「超参」
4. 掌握训练数据的选择、准备、清洗等方法与思路
5. 训练一个垂直领域的大模型

开始上课！


## 还是写在前面

1. 这堂课内容有难度：
   1. 有很多陌生的名词，包括数学名词和模型算法本身的名词
   2. 涉及到很多数学知识，很多东西本身是从数学推导出来的，不好具象化
   3. 深度学习里有大量基于经验的总结，体现成各种超参和 Tricks
2. 这堂课该怎么学：
   1. 注意力集中，跟上我的思路
   2. 遇到不懂的地方，别害怕，先尝试思考
   3. 实现想不明白也别灰心，这个领域的能力积累是需要时间的
   4. 真感兴趣的同学，尝试多度论文，“书读百遍其义自见”的道理我亲自验证过
3. 自己思考很重要！回想“程序员思维向算法工程师思维”的转变


## Fine-Tuning 有什么用：先看一个例子


https://u202774-9847-a4dc9da1.westb.seetacloud.com:8443/

**法律领域的阅读理解**

判决书:

经审理查明:2004 年 1 月 6 日,安居物业与东至县昌盛房地产开发有限责任公司签订前期物业管理服务合同,合同约定由安居物业对东至县昌盛房地产开发有限责任公司开发的食品小区提供物业服务,服务期限为该小区业主大会成立时止,该合同对委托管理事项、双方的权利义务、物业管理服务要求标准、物业管理服务费用、违约责任等进行了具体的约定 2005 年 8 月 28 日,汪 x3 入住该小区 8 栋一单元 102 室,并与安居物业签订了房屋入住协议,约定物业管理费为 252 元/年,并明确若汪 x3 无故不交规定应交费用的,安居物业可要求其限期缴纳并收取应缴费用 3%的滞纳金汪 x3 自 2008 年 8 月 28 日以来未交纳物业服务费,2013 年 12 月,安居物业向汪 x3 下达催交物业服务费通知书现安居物业以被告自 2008 年 8 月 28 日起至 2015 年 4 月 27 日止的物业服务费 1680 元及违约金 50.4 元未交为由诉至本院,被告则以原告不作为为由拒不缴纳,为此成讼另查明,本案所涉食品小区目前未选举业主委员会以上事实有当事人陈述、前期物业管理服务合同、房屋入住协议等证据在卷佐证,足以认定

问题 1: 安居物业给哪个小区做物业？

问题 2: 被告是否如约支付物业费了？


## 我有很多问题

<br/>
<img src="confused.png" style="margin-left: 0px" width="600px">


## 一、什么是：

- 模型训练（Training）
- 预训练（Pre-Training）
- 微调（Fine-Tuning）
- 轻量化微调（Parameter Efficient Fine-Tuning, PEFT）

<br/>
<img src="training.png" style="margin-left: 0px" width="800px">


## 二、什么是模型

<div class="alert alert-warning">
<b>尝试：</b> 用简单的数学语言表达概念
</div>

### 2.1、通俗（不严谨）的说、模型是一个函数：

$y=F(x;\omega)$

- 它接收输入$x$：可以是一个词、一个句子、一篇文章或图片、语音、视频 ...
  - 这些物体都被表示成一个数学「矩阵」（其实应该叫张量，tensor）
- 它预测输出$y$
  - 可以是「是否」（{0,1}）、标签（{0,1,2,3...}）、一个数值（回归问题）、下一个词的概率 ...
- 它的表达式就是网络结构（这里特指深度学习）
- 它有一组参数$\omega$，这就是我们要训练的部分

<div class="alert alert-warning">
<b>把它想象成一个方程：</b> 
    <ol>
        <li>每条数据就是一对儿 $(x,y)$ ，它们是常量</li>
        <li>参数是未知数，是变量</li>
        <li>$F$ 就是表达式：我们不知道真实的公式是什么样的，所以假设了一个足够复杂的公式（比如，一个特定结构的神经网络）</li>
        <li>这个求解这个方程（近似解）就是训练过程</li>
    </ol>
</div>

### 2.2、一个最简单的神经网络

一个神经元：$y=f(\sum_i w_i\cdot x_i)$

<img src="neuron.jpg" style="margin-left: 0px" width="800px">

把很多神经元连接起来，就成了神经网络：$y=f(\sum_i w_i\cdot x_i)$、$z=f(\sum_i w'_i\cdot y_i)$、$\tau=f(\sum_i w''_i\cdot z_i)$、...

<img src="network.jpg" style="margin-left: 0px" width="800px">

这里的$f$叫激活函数，有很多种形式

<img src="activation.jpeg" style="margin-left: 0px" width="800px">

<div class="alert alert-warning">
<b>思考：</b> 这里如果没有激活函数会怎样？
</div>


## 三、什么是模型训练

我们希望找到一组参数$\omega$，使模型预测的输出$\hat{y}=F(x;\omega)$与真实的输出$y$，尽可能的接近

这里，我们（至少）需要两个要素：

- 一个数据集，包含$N$个输入输出的例子（称为样本）：$D=\{(x_i,y_i)\}_{i=1}^N$
- 一个损失函数，衡量模型预测的输出与真实输出之间的差距：$\mathrm{loss}(y,F(x;\omega))$

### 3.1、模型训练本质上是一个求解最优化问题的过程

$\min_{\omega} L(D,\omega)$

$L(D,\omega)=\frac{1}{N}\sum_{i=1}^N\mathrm{loss}(y,F(x;\omega))$

### 3.2、怎么求解

回忆一下梯度的定义

<img src="gradient.svg" style="margin-left: 0px" width="400px">

从最简单的情况说起：梯度下降与凸问题

<img src="gradient.png" style="margin-left: 0px" width="800px">

梯度决定了函数变化的方向，每次迭代更新我们会收敛到一个极值

$\omega_{n+1}\leftarrow \omega_n - \gamma \nabla_{\omega}L(D,\omega)$

其中，$\gamma<1$叫做学习率，它和梯度的模数共同决定了每步走多远

### 3.3、**现实总是没那么简单（1）**：在整个数据集上求梯度，计算量太大了

<br/>
<img src="batch.png" style="margin-left: 0px" width="800px">

<div class="alert alert-success">
<b>划重点：</b>条件允许的情况下，Batch Size尽量大些
</div>

### 3.4、**现实总是没那么简单（2）**：深度学习没有全局最优解（非凸问题）

<br/>
<img src="local_minima.png" style="margin-left: 0px" width="800px">

### 3.5、**现实总是没那么简单（3）**：学习率也很关键，甚至需要动态调整

<br/>
<img src="lr.png" style="margin-left: 0px" width="800px">

<div class="alert alert-success">
<b>划重点：</b>适当调整学习率（Learning Rate），避免陷入很差的局部解或者跳过了好的解
</div>

### 3.6、神经网络的梯度怎么求（选学）

Chain Rule:

假设 $L(w)=f(g(h(w)))$

那么 $L'(w)=f'(g(h(w))) \cdot g'(h(w)) \cdot h'(w)$

<img src="backprop.png" style="margin-left: 0px" width="800px">

蓝色的过程叫 Forward Pass，红色的过程叫 Backward Pass，整个过程叫 Backpropagation

## 四、求解器

为了让训练过程更好的收敛，人们设计了很多更复杂的求解器

- 比如：SGD、L-BFGS、Rprop、RMSprop、Adam、AdamW、AdaGrad、AdaDelta 等等
- 但是，好在最常用的就是 Adam 或者 AdamW

## 五、一些常用的损失函数

- 两个数值的差距，Min Square Error：$\ell_{\mathrm{MSE}}=\frac{1}{N}\sum_{i=1}^N(y_i-\hat{y}_i)^2$ (等价于欧式距离，见下文)
- 两个向量之间的（欧式）距离：$\ell(\mathbf{y},\mathbf{\hat{y}})=\|\mathbf{y}-\mathbf{\hat{y}}\|$
- 两个向量之间的夹角（余弦距离）：
  <img src="cosine_loss.png" style="margin-left: 0px" width="400px">

- 两个概率分布之间的差异，交叉熵：$\ell_{\mathrm{CE}}(p,q)=-\sum_i p_i\log q_i$ ——假设是概率分布 p,q 是离散的
- 这些损失函数也可以组合使用（在模型蒸馏的场景常见这种情况），例如$L=L_1+\lambda L_2$，其中$\lambda$是一个预先定义的权重，也叫一个「超参」

<div class="alert alert-warning">
<b>思考：</b> 你能找到这些损失函数和分类、聚类、回归问题之间的关系吗？
</div>


## 六、用 PyTorch 训练一个最简单的神经网络

数据集（MNIST）样例：

<img src="MNIST.jpg" style="margin-left: 0px" width="800px">

输入一张 28×28 的图像，输出标签 0--9


```python
from __future__ import print_function
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torchvision import datasets, transforms
from torch.optim.lr_scheduler import StepLR

BATCH_SIZE = 64
TEST_BACTH_SIZE = 1000
EPOCHS = 5
LR = 0.01
GAMMA = 0.9
WEIGHT_DECAY = 1e-6
SEED = 42
LOG_INTERVAL = 100

# 定义一个全连接网络


class FeedForwardNet(nn.Module):
    def __init__(self):
        super().__init__()
        # 第一层784维输入、256维输出 -- 图像大小28×28=784
        self.fc1 = nn.Linear(784, 256)
        # 第二层256维输入、128维输出
        self.fc2 = nn.Linear(256, 128)
        # 第三层128维输入、64维输出
        self.fc3 = nn.Linear(128, 64)
        # 第三层64维输入、10维输出 -- 输出类别10类（0,1,...9）
        self.fc4 = nn.Linear(64, 10)

        # Dropout module with 0.2 drop probability
        self.dropout = nn.Dropout(p=0.2)

    def forward(self, x):
        # 把输入展平成1D向量
        x = x.view(x.shape[0], -1)

        # 每层激活函数是ReLU，额外加dropout
        x = self.dropout(F.relu(self.fc1(x)))
        x = self.dropout(F.relu(self.fc2(x)))
        x = self.dropout(F.relu(self.fc3(x)))

        # 输出为10维概率分布
        x = F.log_softmax(self.fc4(x), dim=1)

        return x

# 训练过程


def train(model, loss_fn, device, train_loader, optimizer, epoch):
    # 开启梯度计算
    model.train()
    for batch_idx, (data_input, true_label) in enumerate(train_loader):
        # 从数据加载器读取一个batch
        # 把数据上载到GPU（如有）
        data_input, true_label = data_input.to(device), true_label.to(device)
        # 求解器初始化（每个batch初始化一次）
        optimizer.zero_grad()
        # 正向传播：模型由输入预测输出
        output = model(data_input)
        # 计算loss
        loss = loss_fn(output, true_label)  # F.nll_loss(output, target)
        # 反向传播：计算当前batch的loss的梯度
        loss.backward()
        # 由求解器根据梯度更新模型参数
        optimizer.step()

        # 间隔性的输出当前batch的训练loss
        if batch_idx % LOG_INTERVAL == 0:
            print('Train Epoch: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}'.format(
                epoch, batch_idx * len(data_input), len(train_loader.dataset),
                100. * batch_idx / len(train_loader), loss.item()))


# 计算在测试集的准确率和loss
def test(model, loss_fn, device, test_loader):
    model.eval()
    test_loss = 0
    correct = 0
    with torch.no_grad():
        for data, target in test_loader:
            data, target = data.to(device), target.to(device)
            output = model(data)
            # sum up batch loss
            test_loss += loss_fn(output, target, reduction='sum').item()
            # get the index of the max log-probability
            pred = output.argmax(dim=1, keepdim=True)
            correct += pred.eq(target.view_as(pred)).sum().item()

    test_loss /= len(test_loader.dataset)

    print('\nTest set: Average loss: {:.4f}, Accuracy: {}/{} ({:.0f}%)\n'.format(
        test_loss, correct, len(test_loader.dataset),
        100. * correct / len(test_loader.dataset)))


def main():
    # 检查是否有GPU
    use_cuda = torch.cuda.is_available()

    # 设置随机种子（以保证结果可复现）
    torch.manual_seed(SEED)

    # 训练设备（GPU或CPU）
    device = torch.device("cuda" if use_cuda else "cpu")

    # 设置batch size
    train_kwargs = {'batch_size': BATCH_SIZE}
    test_kwargs = {'batch_size': TEST_BACTH_SIZE}

    if use_cuda:
        cuda_kwargs = {'num_workers': 1,
                       'pin_memory': True,
                       'shuffle': True}
        train_kwargs.update(cuda_kwargs)
        test_kwargs.update(cuda_kwargs)

    # 数据预处理（转tensor、数值归一化）
    transform = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize((0.1307,), (0.3081,))
    ])

    # 自动下载MNIST数据集
    dataset_train = datasets.MNIST('data', train=True, download=True,
                                   transform=transform)
    dataset_test = datasets.MNIST('data', train=False,
                                  transform=transform)

    # 定义数据加载器（自动对数据加载、多线程、随机化、划分batch、等等）
    train_loader = torch.utils.data.DataLoader(dataset_train, **train_kwargs)
    test_loader = torch.utils.data.DataLoader(dataset_test, **test_kwargs)

    # 创建神经网络模型
    model = FeedForwardNet().to(device)

    # 指定求解器
    optimizer = optim.SGD(model.parameters(), lr=LR, weight_decay=WEIGHT_DECAY)
    # scheduler = StepLR(optimizer, step_size=1, gamma=GAMMA)

    # 定义loss函数
    loss_fn = F.cross_entropy

    # 训练N个epoch
    for epoch in range(1, EPOCHS + 1):
        train(model, loss_fn, device, train_loader, optimizer, epoch)
        test(model, loss_fn, device, test_loader)
        # scheduler.step()


if __name__ == '__main__':
    main()
```


<div class="alert alert-warning">
<b>如何运行这段代码：</b>
<ol>
    <li>不要在Jupyter笔记上直接运行</li>
    <li>请将左侧的 exp.py 文件下载到本地</li>
    <li>安装相关依赖包: pip install torch torchvision</li>
    <li>运行：python3 exp.py</li>
</ol>
</div>


## 七、先介绍几个常用的超参

### 7.1、过拟合与欠拟合

<br />
<img src="overfit.png" style="margin-left: 0px" width="800px">

<div class="alert alert-success">
<b>奥卡姆剃刀：</b> 两个处于竞争地位的理论能得出同样的结论，那么简单的那个更好。
</div>

**防止过拟合的方法（1）：**Weight Decay

$J(\omega)=L(D,\omega)+\lambda\|\omega\| \Rightarrow \nabla_{\omega}J=\nabla_{\omega}L + \frac{1}{2}\lambda\omega$

- 惩罚参数的复杂性（$L_2$-norm）：等价与在梯度上减去参数本身（乘一个小数作为权重）
- Weight Decay 就是前面那个权重$\lambda$

**防止过拟合的方法（2）：**Dropout

- 我们在前向传播的时候，概率性的（临时）删除一部分神经元，这样可以使模型泛化性更强，因为它不会太依赖某些局部的特征
- 这样训练$N$次，等价于训练$N$不同的网络，再取平均值；$N$个网络不会同时过拟合于与一个结果，这样平均值的方式能有效减少过拟合的干扰。

<img src="dropout.jfif" style="margin-left: 0px" width="400px">

### 7.2、学习率调整策略

- 开始时学习率大些：快速到达最优解附近
- 逐渐减小学习率：避免跳过最优解
- NLP 任务的损失函数有很多“悬崖峭壁”，自适应学习率更能处理这种极端情况，避免梯度爆炸。

<img src="scheduler.png" style="margin-left: 0px" width="400px">

几种常用的学习率调整器

<img src="lr_scheduler.jpg" style="margin-left: 0px" width="400px">

**防止过拟合的方法（3）：**学习率 Warm Up

先从一个很小的学习率逐渐上升到正常学习率，在稳步减小学习率

- 其原理尚未被充分证明
- 经验主义解释：减缓模型在初始阶段对 mini-batch 的提前过拟合现象，保持分布的平稳
- 经验主义解释：有助于保持模型深层的稳定性

<img src="warmup.png" style="margin-left: 0px" width="400px">

<div class="alert alert-success">
<b>应用场景：</b> (1) 当网络非常容易nan时候；(2) 如果训练集损失很低，准确率高，但测试集损失大，准确率低. 
</div>


## 八、自然语言处理常见的网络结构

<div class="alert alert-warning">
<b>思考：</b> 图像天生可以表示成矩阵（或tensor），那文本怎么表示成矩阵（或tensor）
</div>


### 8.1、文本卷积神经网络 TextCNN

<br />

一个窗口的卷积和Pooling过程

<img src="conv_maxpooling_steps.gif" style="margin-left: 0px" width="600px">

不同大小的窗口分别做卷积和Pooling，结果拼在一起

<img src="TextCNN.jpg" style="margin-left: 0px" width="600px">

- 参数量较少、好训练、算力要求低
- 适合文本分类问题
- 善于表示局部特征（卷积窗口），不擅长表示长上下文依赖关系

### 8.2、循环神经网络 RNN

<br />

首先：输入是一个序列

<img src="RNN.png" style="margin-left: 0px" width="600px">

但这种简易 RNN 有很多问题，最大问题是随着序列长度增加，梯度消失或爆炸

<img src="LSTM.png" style="margin-left: 0px" width="600px">

LSTM 和 GRU 通过「门」来控制上文的状态被记住还是遗忘，同时防止梯度消失或爆炸

以LSTM为例：

<img src="lstm.jfif" style="margin-left: 0px" width="600px">

### 8.3、Attention (for RNN)

<br />

给定当前的输入，上文的一些信息比另一些重要

<img src="attention.gif" style="margin-left: 0px" width="600px">

<br />

<font color='blue'>于是设计一个可微的函数就可以把它加入到网络中来试试，反正也没有全局最优解</font>

<br />
<img src="attention-fn.png" style="margin-left: 0px" width="600px">

- 对当前 token $t$的上文的每个 token $i$计算上述 score
- 将这些 score 做 softmax 得到权重$\alpha_{t,i}$
- 将上文的隐层状态乘以其权重并相加$c_t=\sum_i\alpha_{t,i}h_i$
- 将$c_t$与当前 token 的状态拼接在一起$s_t=\mathrm{concat}(h_t,c_t)$
- 激活输出$y_t=\sigma(s_t)$


## 九、Transformer 江山一统

<div class="alert alert-warning">
<b>思考：</b> RNN有什么缺点？大模型为什么不是很多层RNN？
</div>

<br />
<img src="transformer.gif" style="margin-left: 0px" width="800px">

### 9.1、**消除恐惧：**我们亲手写一个 Transformer

### 9.1.1、Embeddings


In [ ]:
import torch.nn as nn
import torch


class PositionalEmbedding(nn.Module):

    def __init__(self, embed_size, max_len=512):
        super().__init__()

        # Compute the positional encodings once in log space.
        pe = torch.zeros(max_len, embed_size).float()
        pe.require_grad = False

        position = torch.arange(0, max_len).float().unsqueeze(1)
        div_term = (torch.arange(0, embed_size, 2).float()
                    * -(math.log(10000.0) / embed_size)).exp()

        pe[:, 0::2] = torch.sin(position * div_term)
        pe[:, 1::2] = torch.cos(position * div_term)

        pe = pe.unsqueeze(0)
        self.register_buffer('pe', pe)

    def forward(self, x):
        return self.pe[:, :x.size(1)]


class BERTEmbedding(nn.Module):

    def __init__(self, vocab_size, embed_size, dropout=0.1):
        """
        :param vocab_size: 词表大小
        :param embed_size: embedding维度768
        :param dropout: dropout概率
        """
        super().__init__()
        self.token_embedding = nn.Embedding(
            vocab_size, embed_size, padding_idx=0)
        self.position_embedding = PositionalEmbedding(
            embed_size=embed_size, max_len=512)
        self.token_type_embedding = nn.Embedding(2, embed_size, padding_idx=0)
        self.dropout = nn.Dropout(p=dropout)
        self.embed_size = embed_size

    def forward(self, input_ids, token_type_ids):
        x = self.token_embedding(input_ids) + self.position_embedding(
            input_ids) + self.token_type_embedding(token_type_ids)
        return self.dropout(x)

### 9.1.2、单头 Attention


In [ ]:
import torch.nn as nn
import torch.nn.functional as F
import torch

import math

'''
query = query_linear(x)
key = key_linear(x)
value = value_linear(x)
'''

# 单个头的注意力计算


class Attention(nn.Module):

    def forward(self, query, key, value, mask=None, dropout=None):
        scores = torch.matmul(query, key.transpose(-2, -1)) \
            / math.sqrt(query.size(-1))

        if mask is not None:
            scores = scores.masked_fill(mask == 0, -1e9)

        p_attn = F.softmax(scores, dim=-1)

        if dropout is not None:
            p_attn = dropout(p_attn)

        return torch.matmul(p_attn, value), p_attn

<br />
每个token对应的query向量与每个token对应的key向量做内积

<img src="kq2.gif" style="margin-left: 0px" width="800px">

<br />
将上述内积取softmax（得到0~1之间的值，即为attention权重）

<img src="kq_softmax.gif" style="margin-left: 0px" width="800px">

<br />
计算每个token相对于所有其它token的attention权重（最终构成一个$L\times L$的attention矩阵）

<img src="kq_softmax2.gif" style="margin-left: 0px" width="800px">

<br />
每个token对应的value向量乘以attention权重，并相加，得到当前token的self-attention value向量

<img src="v.gif" style="margin-left: 0px" width="800px">

<br />
将上述操作应用于每个token
<img src="v2.gif" style="margin-left: 0px" width="800px">

<br />
以上是一个头的操作，同时（并行）应用于多个独立的头


### 9.1.3、多头 Attention

将每个头得到向量拼接在一起，最后乘一个线性矩阵，得到 multi-head attention 的输出

<img src="multi-head.gif" style="margin-left: 0px" width="800px">


In [ ]:
import torch.nn


class MultiHeadedAttention(nn.Module):
    def __init__(self, head_num, hidden_size, dropout=0.1):
        """
        :param head_num: 头的个数，必须能被hidden_size整除
        :param hidden_size: 隐层的维度，与embed_size一致
        """
        super().__init__()
        assert hidden_size % head_num == 0

        self.per_head_dim = hidden_size // head_num
        self.head_num = head_num
        self.hidden_size = hidden_size

        self.query_linear = nn.Linear(hidden_size, hidden_size)
        self.key_linear = nn.Linear(hidden_size, hidden_size)
        self.value_linear = nn.Linear(hidden_size, hidden_size)

        self.output_linear = nn.Linear(hidden_size, hidden_size)
        self.attention = Attention()

        self.dropout = nn.Dropout(p=dropout)

    def reshape(self, x, batch_size):
        # 拆成多个头
        return x.view(batch_size, -1, self.head_num, self.per_head_dim).transpose(1, 2)

    def forward(self, x, mask=None):
        batch_size = x.size(0)

        query = self.reshape(self.query_linear(x))
        key = self.reshape(self.key_linear(x))
        value = self.reshape(self.value_linear(x))

        # 每个头计算attention
        x, attn = self.attention(
            query, key, value, mask=mask, dropout=self.dropout
        )

        # 把每个头的attention*value拼接在一起
        x = x.transpose(1, 2).contiguous().view(
            batch_size, -1, self.hidden_size)

        # 乘一个线性矩阵
        return self.output_linear(x)

### 9.1.4、全连接网络（Feed-Forward Network）


In [ ]:
import torch.nn as nn


class FeedForward(nn.Module):

    def __init__(self, hidden_size, dropout=0.1):
        super(FeedForward, self).__init__()
        self.input_layer = nn.Linear(hidden_size, hidden_size*4)
        self.output_layer = nn.Linear(hidden_size*4, hidden_size)
        self.dropout = nn.Dropout(dropout)
        self.activation = nn.GELU()

    def forward(self, x):
        x = self.input_layer(x)
        x = self.activation(x)
        x = self.dropout(x)
        x = self.output_layer(x)
        return x

### 9.1.5、拼成一层 Transformer


In [ ]:
import torch.nn as nn


class TransformerBlock(nn.Module):

    def __init__(self, hidden_size, head_num, dropout=0.1):
        super().__init__()
        self.multi_head_attention = MultiHeadedAttention(head_num, hidden_size)
        self.feed_forward = FeedForward(hidden_size, dropout=dropout)
        self.layer_norm1 = nn.LayerNorm(hidden_size)
        self.dropout1 = nn.Dropout(dropout)
        self.layer_norm2 = nn.LayerNorm(hidden_size)
        self.dropout2 = nn.Dropout(dropout)
        self.dropout = nn.Dropout(p=dropout)

    def forward(self, x, mask):
        x0 = x
        # 多头注意力层
        x = self.multi_head_attention(x, mask)

        # 残差和LayerNorm层(1)
        x = self.dropout1(x)
        x = self.layer_norm1(x0+x)

        # 前向网络层
        x1 = x
        x = self.feed_forward(x)

        # 残差和LayerNorm层(2)
        x = self.dropout2(x)
        x = self.layer_norm2(x1+x)
        return x

<br />
Multi-head attention的输出，经过残差和norm之后进入一个两层全连接网络
<img src="ffn.gif" style="margin-left: 0px" width="800px">


Layernorm:

$y=\frac{x-\mathrm{E}(x)}{\sqrt{\mathrm{Var}(x)+\epsilon}}*\gamma+\beta$

其中 $\gamma$ 和 $\beta$ 是可训练的参数，$\epsilon=10^{-5}$是超参，保持数值稳定性。

### 9.1.6、多层 Transformer 构成 BERT Encoder


In [ ]:
import torch.nn as nn


class BERT(nn.Module):

    def __init__(self, vocab_size, hidden_size=768, layer_num=12, head_num=12, dropout=0.1):

        super().__init__()
        # Embedding层
        self.embedding = BERTEmbedding(
            vocab_size=vocab_size, embed_size=hidden_size)
        # N层Transformers
        self.transformer_blocks = nn.ModuleList(
            [TransformerBlock(hidden_size, head_num, dropout)
             for _ in range(layer_num)]
        )

    def forward(self, input_ids, token_type_ids):
        """
        tokenizer(["你好吗","你好"], text_pair=["我很好","我好"], max_length=10, padding='max_length',truncation=True)
        [CLS]你好吗[SEP]我很好[SEP][PAD]
        [CLS]你好[SEP]我好[SEP][PAD][PAD][PAD]  
        input_ids: [
            [101, 872, 1962, 1408, 102, 2769, 2523, 1962, 102, 0],
            [101, 872, 1962, 102, 2769, 1962, 102, 0, 0, 0]
        ]
        token_type_ids：[
                [0, 0, 0, 0, 0, 1, 1, 1, 1, 0],
                [0, 0, 0, 0, 1, 1, 1, 0, 0, 0]
            ]
        """
        attention_mask = (x > 0).unsqueeze(
            1).repeat(1, x.size(1), 1).unsqueeze(1)

        # 计算embedding
        x = self.embedding(input_ids, token_type_ids)

        # 逐层代入Tranformers
        for transformer in self.transformer_blocks:
            x = transformer.forward(x, attention_mask)

        return x

### 9.2 Transformer 怎么用

### 9.2.1. Encoder-Only LM 用于文本表示

针对不同下游任务，在 Encoder 上面添加不同的输出层
<br />
<img src="BERT.png" style="margin-left: 0px" width="600px">

BERT-BiLSTM-CRF一个序列标注的经典网络结构

<img src="bert-bilstm-crf.jpg" style="margin-left: 0px" width="600px">

### 9.2.2. Encoder-Decoder LM，机器翻译/文本生成（大语言模型的一种形态）

- Decoder 也是 N 层 transformer 结构
- 生成一个 token，把它加入上文，再生成下一个 token，以此类推
  <br />
  <img src="decoder1.png" style="margin-left: 0px" width="600px">

Decoder 的每个 token 与 encoder 最后一层的输出和 decoder 上文的 token 一起做 attention
<br />
<img src="decoder2.png" style="margin-left: 0px" width="600px">

Decoder 的 token 只能 attend 到上文的 token（因为此时下文还没有出现）
<br />
<img src="decoder3.png" style="margin-left: 0px" width="600px">

### 9.2.3. Decoder-Only LM 也叫 Causal LM 或 Left-to-right LM（GPT 家族）

<br />
<img src="decoder4.png" style="margin-left: 0px" width="400px">

### 9.2.4. 大语言模型族谱

<br />
<img src="llm.jpg" style="margin-left: 0px" width="800px">


[继续](huggingface/index.ipynb)
